In [1]:
import smtplib
import ssl
import pyodbc
import configparser
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
import matplotlib.ticker as mtick
import seaborn as sns
from email.message import EmailMessage
from email.utils import make_msgid
from email.mime.image import MIMEImage
from pathlib import Path
from datetime import datetime, time

In [2]:
config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\CODIGOS\relatório_improdutivo\credenciais.ini")

# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

# 1. Criar dados fictícios e gerar Excel
query = '''
SELECT 
    cd.Ciclo,
    min(emh.data_estoque)
FROM estoque_mar_historico emh
INNER JOIN ciclos_data_2025 cd 
    ON cd.[Date] = emh.data_estoque and emh.data_estoque > '2025-06-19'
GROUP BY cd.Ciclo
'''
datas = pd.read_sql(query, conn)

conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_15612\775955969.py:22: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  datas = pd.read_sql(query, conn)


In [3]:
lista = datas.iloc[:, 1].tolist()
lista

['2025-06-20', '2025-06-26', '2025-07-16', '2025-08-06']

In [4]:
datas_lista = datas.iloc[:, 1].tolist()  # sua lista de datas

# monta os placeholders
placeholders = ", ".join(["?"] * len(datas_lista))


In [5]:
# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

query = f"""
SELECT 
    emh.PDV,
    emh.SKU,
    emh.[ESTOQUE ATUAL],
    emh.[ESTOQUE EM TRANSITO],
    emh.[PEDIDO PENDENTE],
    emh.[DDV PREVISTO],
    cd.Ciclo,
    emh.data_estoque
FROM estoque_mar_historico emh
INNER JOIN ciclos_data_2025 cd 
    ON cd.[Date] = emh.data_estoque and cd.MARCA ='BOT'
WHERE emh.data_estoque IN ({placeholders})
"""

estoque_data = pd.read_sql(query, conn, params=datas_lista)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_15612\485056913.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  estoque_data = pd.read_sql(query, conn, params=datas_lista)


In [6]:
estoque_data.head()

PDV    SKU ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0  20968  94394             0                   0               0   
1  20969  94394             0                   0               0   
2  20970  94394             0                   0               0   
3  20986  94394             0                   0               0   
4  20988  94394             0                   0               0   

  DDV PREVISTO    Ciclo data_estoque  
0         None  C202509   2025-06-26  
1         None  C202509   2025-06-26  
2         None  C202509   2025-06-26  
3         None  C202509   2025-06-26  
4         None  C202509   2025-06-26

In [7]:
# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

query = f"""
SELECT 
    d.loja_id AS PDV,
    cast(d.code as int) as SKU,
    d.codcategory AS CATEGORIA,
    d.salescurve AS Curva,
    d.isproductdeactivated AS Desativado,
    d.criticalitem_iscritical AS Item_Critico,
    d.[data] as data_estoque
from draft_historico d
where d.[data] in ({placeholders})
"""

draft_data = pd.read_sql(query, conn, params=datas_lista)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_15612\731793387.py:22: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  draft_data = pd.read_sql(query, conn, params=datas_lista)


In [8]:
draft_data.head()

PDV    SKU         CATEGORIA Curva Desativado Item_Critico data_estoque
0  20986  51470  CUIDADOS FACIAIS     C          0            0   2025-06-20
1  12826  86340         MAQUIAGEM     E          0            0   2025-06-20
2  21278  58334         MAQUIAGEM     B          0            0   2025-06-20
3  20995  57761             SOLAR     E          0            0   2025-06-20
4  24254  75568         MAQUIAGEM     C          0            0   2025-06-20

In [9]:
draft_data['SKU'] = draft_data['SKU'].astype(str)

draft_data['SKU'].head()

0    51470
1    86340
2    58334
3    57761
4    75568
Name: SKU, dtype: object

In [10]:
df_junto = pd.merge(estoque_data,draft_data,on =['PDV',	'SKU','data_estoque'],how='inner')

df_junto.head()

PDV    SKU ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0  21277  88146             0                   0               0   
1   3546  87960             8                   0               0   
2   4560  87960             3                   0               0   
3   5699  87960             4                   0               0   
4  12522  87960             0                   1               0   

  DDV PREVISTO    Ciclo data_estoque  CATEGORIA Curva Desativado Item_Critico  
0            0  C202509   2025-06-20  MAQUIAGEM     E          0            0  
1         0.07  C202509   2025-06-20  MAQUIAGEM     C          0            0  
2         0.07  C202509   2025-06-20  MAQUIAGEM     C          0            0  
3         0.05  C202509   2025-06-20  MAQUIAGEM     C          0            0  
4         0.04  C202509   2025-06-20  MAQUIAGEM     C          0            0

In [11]:
from datetime import datetime
from dateutil.relativedelta import relativedelta

# Pegar a primeira data
primeira_data = datetime.strptime(datas_lista[0], "%Y-%m-%d")

# Subtrair 1 mês
data_inicio = primeira_data - relativedelta(months=1)

# Formatar para string no formato SQL Server (YYYY-MM-DD)
data_inicio_str = data_inicio.strftime("%Y-%m-%d")

In [12]:
data_inicio_str

'2025-05-20'

In [13]:
# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

query = """
SELECT
  fne.cnpj_destinatario,
  fne.cnf AS Nota_Fiscal,
  fne.data_emissao,
  fnei.codigo_pedido,
  fnei.n_item,
  fnei.cod_produto,
  fnei.produto,
  fnei.quantidade,
  fnei.valor_unitario,
  fnei.valor_total_produtos,
  b.PDV,
  p.quantity_accepted as qtd_aceita_industria,
  p.status 
FROM fato_notas_entrada fne
INNER JOIN fato_notas_entrada_itens fnei ON fne.chave = fnei.chave
INNER JOIN base_pdvs b ON fne.cnpj_destinatario = b.CNPJ
LEFT JOIN (
    SELECT
      sellOrders,
      sku,
      storeCode,
      MAX(quantity_accepted) AS quantity_accepted,
      MAX(status) AS status,
      MAX(pedido_id) AS pedido_id,
      MAX([date]) AS [date],
      MAX(deliveryDate) AS deliveryDate
    FROM produtos_pedidos
    GROUP BY sellOrders, sku, storeCode
) p 
  ON p.sellOrders = fnei.codigo_pedido 
 AND p.sku = fnei.cod_produto 
 AND p.storeCode = b.PDV 
WHERE fne.data_emissao >= ?
"""

pedidos = pd.read_sql(query, conn, params=[data_inicio_str])
conn.close()





C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_15612\1525897645.py:46: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  pedidos = pd.read_sql(query, conn, params=[data_inicio_str])


In [14]:
datas_lista[0]

'2025-06-20'

In [15]:
pedidos.head()

cnpj_destinatario Nota_Fiscal data_emissao codigo_pedido  n_item  \
0    08489643005545   000806049   2025-05-24    0163731443       3   
1    08489643006193   000806913   2025-05-27    0163731450       3   
2    08489643006193   000806913   2025-05-27    0163731450       4   
3    08489643004654   000806533   2025-05-27    0163731452      10   
4    08489643005898   000806995   2025-05-27    0163731459       2   

  cod_produto                      produto  quantidade  valor_unitario  \
0       86019            ESTJ ARBO AMOR 25           4         59.1150   
1       85294  ESTJ QUASAR CLASSIC AMOR/25          10         55.6330   
2       85294  ESTJ QUASAR CLASSIC AMOR/25           5         55.6320   
3       86019            ESTJ ARBO AMOR 25          24         59.1163   
4       85293        ESTJ HER CODE AMOR/25          24        121.9821   

   valor_total_produtos    PDV  qtd_aceita_industria status  
0                236.46  20986                   NaN   None  
1                556.33  20991                   NaN   None  
2                278.16  20991                   NaN   None  
3               1418.79  20993                   NaN   None  
4               2927.57  20997                   NaN   None